In [1]:
import pickle, textwrap
from pathlib import Path

# ── where the pickle lives ─────────────────────────────────────────────
pkl_path = Path("output/data/recalled_stories.pkl")

with pkl_path.open("rb") as f:
    artefact = pickle.load(f)

stories = artefact["recalled_stories"]          # main dict
details = artefact.get("details_used", {})      # optional dict

variants = [
    ("IMAGINED",  "imagined"),
    ("GIST-0",             0),
    ("+1",                 1),
    ("+3",                 3),
    ("FULL",       "full"),
]

wrap = lambda s: textwrap.fill(s, 90, subsequent_indent=" " * 11)

for idx, orig in enumerate(stories["full"]):
    divider = f"\n==== STORY {idx} {'='*60}"
    print(divider)
    print("ORIGINAL :", wrap(orig))

    for tag, key in variants:
        txt = stories[key][idx]
        print(f"{tag:<10}: {wrap(txt)}")

        # show the cue-phrases, if stored in the pickle
        if key in (1, 3) and key in details:
            cues = details[key][idx]
            if cues:                         # non-empty?
                cue_str = ";  ".join(cues)
                print(f"{'':<10}  ↳ details_used: {cue_str}")

print("\nDone. Total stories:", len(stories['full']))



==== STORY 0 ============================================================
ORIGINAL : Susan really likes to have coffee in the morning and drinks it daily. One morning Susan
           realized she was out and had to go buy more. She found a store nearby that had
           a special coffee blend. She was so excited when she brewed her new coffee.
           After brewing her coffee she took a sip and sighed happily.
IMAGINED  : [INST] Susan really likes to have coffee in the morning and drinks it daily. What happened
           (in detail)? [/INST] Susan is an individual who has developed a daily habit of
           enjoying a cup of coffee in the morning. This routine likely begins as soon as
           she wakes up, signifying the start of her day. Here's a detailed description of
           what might happen:  1. Alarm goes off: The first thing Susan does in the
           morning is to wake up from her sleep. Her alarm clock goes off, signaling the
           end of her night's re

In [2]:
import pickle, textwrap
from pathlib import Path

DATA_DIR = Path("output/data")

enc_path  = DATA_DIR / "recalled_stories.pkl"
con_path  = DATA_DIR / "consolidation_recall.pkl"

forg_path = DATA_DIR / "forgetting_multi.pkl"

enc  = pickle.load(open(enc_path, "rb"))

con  = pickle.load(open(con_path, "rb")) if con_path.exists() else None
forg = pickle.load(open(forg_path, "rb")) if forg_path.exists() else None

orig_list   = enc["recalled_stories"]["full"]
rec_variants = enc["recalled_stories"]          # dict: imagined/0/1/3/full
con_epochs   = con["epoch_recalls"] if con else []   # list[epoch][story]
forg_recs    = []

if forg:
    eps = forg.get("recalls")
    if eps and isinstance(eps[0], str):
        eps = [eps]
    forg_recs = eps or []

wrap = lambda s: textwrap.fill(s, 100, subsequent_indent=" " * 12)

# print everything
for idx, orig in enumerate(orig_list):
    hdr = f" STORY {idx} ".center(90, "=")
    print(hdr)
    print("ORIGINAL :", wrap(orig))

    # baseline recalls
    for tag, key in [("IMAGINED", "imagined"),
                     ("GIST-0",            0),
                     ("+1",                1),
                     ("+3",                3),
                     ("FULL",     "full")]:
        print(f"{tag:<10}: {wrap(rec_variants[key][idx])}")

    # consolidation epochs
    if con_epochs:
        print("\n-- CONSOLIDATION ---------------------------------------------")
        for e, epoch in enumerate(con_epochs, start=1):
            print(f"Epoch {e:02d}: {wrap(epoch[idx])}")

    #forgetting episodes
    if forg_recs:
        print("\n-- FORGETTING -----------------------------------------------")
        for ep, episode in enumerate(forg_recs):
            print(f"Episode {ep:02d}: {wrap(episode[idx])}")

print("\nDone. Total stories printed:", len(orig_list))


======================================== STORY 0 =========================================
ORIGINAL : Susan really likes to have coffee in the morning and drinks it daily. One morning Susan realized she
            was out and had to go buy more. She found a store nearby that had a special coffee
            blend. She was so excited when she brewed her new coffee. After brewing her coffee she
            took a sip and sighed happily.
IMAGINED  : [INST] Susan really likes to have coffee in the morning and drinks it daily. What happened (in
            detail)? [/INST] Susan is an individual who has developed a daily habit of enjoying a
            cup of coffee in the morning. This routine likely begins as soon as she wakes up,
            signifying the start of her day. Here's a detailed description of what might happen:  1.
            Alarm goes off: The first thing Susan does in the morning is to wake up from her sleep.
            Her alarm clock goes off, signaling the end of h

IOPub data rate exceeded.
The Jupyter server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--ServerApp.iopub_data_rate_limit`.

Current values:
ServerApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
ServerApp.rate_limit_window=3.0 (secs)



In [5]:
import pickle, random
from pathlib import Path
import textwrap

DATA_DIR = Path("output/data")

# load all the necessary pickles
stories_data = pickle.load(open(DATA_DIR/"recalled_stories.pkl", "rb"))
con_data     = pickle.load(open(DATA_DIR/"consolidation_recall.pkl", "rb"))
forg_path    = (DATA_DIR/"forgetting_multi.pkl"
                if (DATA_DIR/"forgetting_multi.pkl").exists()
                else DATA_DIR/"forgetting.pkl")
forg_data    = pickle.load(open(forg_path, "rb"))

# choose one story index (or hard-code e.g. idx = 0)
n = len(stories_data["recalled_stories"]["full"])
idx = random.randrange(n)

# extract texts
orig        = stories_data["recalled_stories"]["full"][idx]
encoded0    = stories_data["recalled_stories"][0][idx]

# consolidation recalls:
# epoch_recalls is a list of lists: [ [stories@epoch1], [stories@epoch2], … ]
con_epochs  = con_data["epoch_recalls"]
con_early   = con_epochs[0][idx]
con_late    = con_epochs[-1][idx]

# forgetting recalls:
# "recalls" is a list of episodes: [baseline, ep1, ep2, …]
forg_recs   = forg_data["recalls"]
if forg_recs and isinstance(forg_recs[0], str):
    forg_recs = [forg_recs]       # wrap legacy single‐episode form
# pick first real episode as “early”
early_i     = 1 if len(forg_recs) > 1 else 0
late_i      = len(forg_recs) - 1
forg_early  = forg_recs[early_i][idx]
forg_late   = forg_recs[late_i][idx]

# simple LaTeX-escaping for underscores & ampersands
def esc(s):
    return (s.replace("\\", "\\textbackslash{}")
             .replace("_", "\\_")
             .replace("&", "\\&")
             .replace("%", "\\%"))

# wrap long text into paragraphs so your table cells don’t overflow
wrap = lambda txt: textwrap.fill(esc(txt), 60, subsequent_indent="")

# ── emit the table ─────────────────────────────────────────────────────
col_width = "p{0.15\\linewidth}"
fmt = "|" + "|".join([col_width]*6) + "|"

print(r"\begin{table}[ht]")
print(r"\footnotesize")
print(r"\centering")
print(r"\renewcommand{\arraystretch}{1.3}")
print(r"\begin{tabular}{" + fmt + "}")
print(r"\hline")
print(r"\textbf{Original} & "
      r"\textbf{Encoded (0-detail)} & "
      r"\textbf{Cons. (early)} & "
      r"\textbf{Cons. (late)} & "
      r"\textbf{Forget (early)} & "
      r"\textbf{Forget (late)} \\ \hline")
print(f"{wrap(orig)} &")
print(f"{wrap(encoded0)} &")
print(f"{wrap(con_early)} &")
print(f"{wrap(con_late)} &")
print(f"{wrap(forg_early)} &")
print(f"{wrap(forg_late)} \\\\ \\hline")
print(r"\end{tabular}")
print(r"\caption[One‐story consolidation & forgetting]{"
      r"Text trajectories for one randomly selected story: original, "
      r"0‐detail encoding, early vs late consolidation, and early vs late forgetting.}")
print(r"\label{table:one_story_traj}")
print(r"\end{table}")


\begin{table}[ht]
\footnotesize
\centering
\renewcommand{\arraystretch}{1.3}
\begin{tabular}{|p{0.15\linewidth}|p{0.15\linewidth}|p{0.15\linewidth}|p{0.15\linewidth}|p{0.15\linewidth}|p{0.15\linewidth}|}
\hline
\textbf{Original} & \textbf{Encoded (0-detail)} & \textbf{Cons. (early)} & \textbf{Cons. (late)} & \textbf{Forget (early)} & \textbf{Forget (late)} \\ \hline
Rick and Sue didn't have any children. They had a pair of
stuffed monkeys that they called their kids. They always
took their monkeys on vacation with them. They took pictures
of their monkeys wherever they went. They enjoyed showing
their friends an album full of monkey photos. &
Rick and Sue didn't have any children. They didn't want any
children. They didn't adopt any children. They didn't have
any pets. They didn't have any nieces or nephews. They
didn't have any godchildren. They didn't have any friends
with children. They didn't have any interest in children.
They didn't have any plans to have children. They didn't
ha